In [1]:
pip install airfoils

Note: you may need to restart the kernel to use updated packages.


In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib import style
style.use('seaborn-ticks')
from matplotlib.animation import FFMpegWriter
from airfoils import Airfoil
from scipy import interpolate
from tqdm import tqdm
%matplotlib osx

### Defining constants for airfoil equation

In [2]:
airfoil_x= np.linspace(0,1,1000)
k0=0.2969
k1=0.1260
k2=0.3516
k3=0.283
k4=0.105
thickness = 44/100

plot_x_len=400
plot_y_len=100

### Defining necessary functions to draw & fill and airfoil in imshow

In [3]:
def airfoil(x_len,x_shift,y_len,y_shift):
    t=thickness #Thickness of airfoil
    x = airfoil_x
    y= 5*t*(k0*np.sqrt(x)-k1*x-k2*x**2+k3*x**3-k4*x**4)
    xs_top = (x*x_len)+x_shift
    ys_top = (y*y_len)+y_shift
    xs_bottom = (x*x_len)+x_shift
    ys_bottom = (-y*y_len)+y_shift
    return xs_top, ys_top, xs_bottom, ys_bottom

xs_top,ys_top,xs_bottom,ys_bottom = airfoil(100,80,20,50)

In [4]:
x_min = min(xs_top)
x_max = max(xs_top)

x_length_airfoil = np.arange(x_min,x_max+1,1)
x_length_airfoil_shifted = x_length_airfoil-min(x_length_airfoil)
x_convert_airfoil = x_length_airfoil_shifted/max(x_length_airfoil_shifted)

In [5]:
def airfoil_single(x_val,y_len,y_shift):
    index=np.where(x_length_airfoil == x_val)[0]
    index_true=index[0]
    x = x_convert_airfoil[index_true]
    t = thickness
    y_value = 5*t*(k0*np.sqrt(x)-k1*x-k2*x**2+k3*x**3-k4*x**4)
    y_top = (y_value*y_len)+y_shift
    y_bottom = (-y_value*y_len)+y_shift
    return y_top,y_bottom

In [6]:
array_test=np.zeros((plot_y_len,plot_x_len))
for y in range(0,plot_y_len):
    for x in range(0,plot_x_len):
        if x <= max(xs_top) and x >= min(xs_top):
            if y <= airfoil_single(x,20,50)[0] and y >= airfoil_single(x,20,50)[1]:
                array_test[y,x] = 1
for y in range(0,plot_y_len):
    for x in range(0,plot_x_len):
        if array_test[y,x] == 1 and array_test[y+1,x] == 0:
            array_test[y,x] = 100
        elif array_test[y,x] == 1 and array_test[y-1,x] == 0:
            array_test[y,x] = 100

### Testing Airfoil Plotting

In [23]:
np.max(array_test)

1.0

In [26]:
plt.imshow(array_test)
plt.show()

### Defining simulation constants

In [7]:
plot_x_len=400
plot_y_len=100
Tau = 0.53 #Kinematic timescale
time_iterations=7000
plot_iterations=50

### Using Lattice Boltzmann Method for fluid dynamics, defining actual lattice for each particle

In [8]:
Number_of_lattice_particles = 9
lattice_x_positions = np.array([0,0,1,1,1,0,-1,-1,-1])
lattice_y_positions = np.array([0,1,1,0,-1,-1,-1,0,1])
lattice_movement_weights = np.array([4/9,1/9,1/36,1/9,1/36,1/9,1/36,1/9,1/36])

#The positions are equivalent to the velocity indices

### Defining Intitial Conditions & adding random variations in the fluid

In [9]:
randomness_cst = 0.1

Initial_conditions = np.ones((plot_y_len,plot_x_len,Number_of_lattice_particles))+randomness_cst*np.random.rand(plot_y_len,plot_x_len,Number_of_lattice_particles)
Initial_conditions[:,:,3] = 2.3
Initial_with_randomness_and_movement=Initial_conditions

Main_array = np.copy(Initial_with_randomness_and_movement)

### Defining the plot space with airfoil inside

In [10]:
plot_shape = np.full((plot_y_len,plot_x_len),False)
for y in range(0,plot_y_len):
    for x in range(0,plot_x_len):
        if x <= max(xs_top) and x >= min(xs_top):
            if y <= airfoil_single(x,20,50)[0] and y >= airfoil_single(x,20,50)[1]:
                plot_shape[y,x] = True

In [11]:
array_test=np.zeros((plot_y_len,plot_x_len))
for y in range(0,plot_y_len):
    for x in range(0,plot_x_len):
        if x <= max(xs_top) and x >= min(xs_top):
            if y <= airfoil_single(x,20,50)[0] and y >= airfoil_single(x,20,50)[1]:
                array_test[y,x] = 1
for y in range(0,plot_y_len):
    for x in range(0,plot_x_len):
        if array_test[y,x] == 1 and array_test[y+1,x] == 0:
            array_test[y,x] = 10000
        elif array_test[y,x] == 1 and array_test[y-1,x] == 0:
            array_test[y,x] = 10000

### Main time loop for true airflow

In [46]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len,plot_x_len,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len,plot_x_len,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil Testing', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_V5.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape,:] = Collision_boundary_final
        momentum_x[plot_shape] = 0
        momentum_y[plot_shape] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            plt.clf()
            plt.imshow(np.sqrt(momentum_x**2+momentum_y**2),cmap='bone')
            plt.imshow(array_test,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()

100%|██████████| 7000/7000 [02:18<00:00, 50.37it/s]


### Main loop for vorticity in airflow

In [53]:
time_iterations=7000
plot_iterations=50

In [54]:
Initial = np.ones((plot_y_len,plot_x_len,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len,plot_x_len,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

metadata = dict(title='Lattice Boltzmann Fluid Vorticity Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Vorticity_V3.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]

        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape,:] = Collision_boundary_final
        momentum_x[plot_shape] = 0
        momentum_y[plot_shape] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            curl_x = momentum_x[2:,1:-1] - momentum_x[0:-2,1:-1]
            curl_y = momentum_y[1:-1,2:] - momentum_y[1:-1,0:-2]
            curl=curl_x-curl_y
            plt.clf()
            plt.imshow(curl,cmap='seismic')
            plt.imshow(array_test,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()

100%|██████████| 7000/7000 [02:21<00:00, 49.60it/s]


### Rotated Airfoil Testing

In [43]:
x_mid=np.median(xs_top)-20
y_low=min(ys_bottom)
y_high=max(ys_top)
y_mid=((y_high-y_low)//2)+y_low

In [44]:
x_top_rotation=(((xs_top-x_mid)*np.cos(np.pi/6))+x_mid)+(((ys_top-y_mid)*np.sin(np.pi/6))+y_mid)
y_top_rotation=(((xs_top-x_mid)*-np.sin(np.pi/6))+x_mid)+(((ys_top-y_mid)*np.cos(np.pi/6))+y_mid)
x_bottom_rotation=(((xs_bottom-x_mid)*np.cos(np.pi/6))+x_mid)+(((ys_bottom-y_mid)*np.sin(np.pi/6))+y_mid)
y_bottom_rotation=(((xs_bottom-x_mid)*-np.sin(np.pi/6))+x_mid)+(((ys_bottom-y_mid)*np.cos(np.pi/6))+y_mid)

In [45]:
x_min_r = int(min(x_top_rotation))
x_max_r = int(max(x_top_rotation))

x_length_airfoil_r = np.arange(x_min_r,x_max_r+1)
x_length_airfoil_shifted_r = x_length_airfoil_r-min(x_length_airfoil_r)
x_convert_airfoil_r = x_length_airfoil_shifted_r/max(x_length_airfoil_shifted_r)

In [46]:
x_length_airfoil_r

array([133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145,
       146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158,
       159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171,
       172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184,
       185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197,
       198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210,
       211, 212, 213, 214, 215, 216, 217, 218, 219, 220])

In [47]:
def airfoil_single_r(x_val,y_len,y_shift):
    index=np.where(x_length_airfoil_r == x_val)[0]
    index_true=index[0]
    x = x_convert_airfoil_r[index_true]
    x_value=x_val
    t = thickness
    y_value = 5*t*(k0*np.sqrt(x)-k1*x-k2*x**2+k3*x**3-k4*x**4)
    y_top = (y_value*y_len)+y_shift
    y_top_r=(((x_value-x_mid)*np.sin(np.pi/6))+x_mid)+(((y_top-y_mid)*np.cos(np.pi/6))+y_mid)
    y_bottom = (-y_value*y_len)+y_shift
    y_bottom_r=(((x_value-x_mid)*np.sin(np.pi/6))+x_mid)+(((y_bottom-y_mid)*np.cos(np.pi/6))+y_mid)
    return y_top_r,y_bottom_r

In [48]:
plot_y_len_r=200
plot_x_len_r=400
array_test_r=np.zeros((plot_y_len_r,plot_x_len_r))
xs_used=[]
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if x <= int(max(x_top_rotation)) and x >= int(min(x_top_rotation)):
            xs_used.append(x)
            if y <= airfoil_single_r(x,20,0)[0] and y >= airfoil_single_r(x,20,0)[1]:
                array_test_r[y-50,x] = 1
xs_used=np.unique(xs_used)

In [50]:
plt.imshow(array_test_r)
plt.show()

### Roated Airfoil Plotting

In [49]:
time_iterations=7000
plot_iterations=50

In [50]:
plot_shape_r = np.full((plot_y_len_r,plot_x_len_r),False)
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if x <= int(max(x_top_rotation)) and x >= int(min(x_top_rotation)):
            if y <= airfoil_single_r(x,20,0)[0] and y >= airfoil_single_r(x,20,0)[1]:
                plot_shape_r[y-50,x] = True

In [51]:
array_test_r=np.zeros((plot_y_len_r,plot_x_len_r))
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if x <= int(max(x_top_rotation)) and x >= int(min(x_top_rotation)):
            if y <= airfoil_single_r(x,20,0)[0] and y >= airfoil_single_r(x,20,0)[1]:
                array_test_r[y-50,x] = 1
                
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if array_test_r[y,x] == 1 and array_test_r[y+1,x] == 0:
            array_test_r[y,x] = 10000
        elif array_test_r[y,x] == 1 and array_test_r[y-1,x] == 0:
            array_test_r[y,x] = 10000

In [57]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len_r,plot_x_len_r,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len_r,plot_x_len_r,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Roated_Airfoil_V7.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape_r,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape_r,:] = Collision_boundary_final
        momentum_x[plot_shape_r] = 0
        momentum_y[plot_shape_r] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            plt.clf()
            plt.imshow(np.sqrt(momentum_x**2+momentum_y**2),cmap='bone')
            plt.imshow(array_test_r,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.05)
            writer.grab_frame()

100%|██████████| 7000/7000 [04:49<00:00, 24.16it/s]


### Rotated Airfoil Vorticity

In [52]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len_r,plot_x_len_r,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len_r,plot_x_len_r,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Roated_Airfoil_Vorticity_V3.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape_r,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape_r,:] = Collision_boundary_final
        momentum_x[plot_shape_r] = 0
        momentum_y[plot_shape_r] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            curl_x = momentum_x[2:,1:-1] - momentum_x[0:-2,1:-1]
            curl_y = momentum_y[1:-1,2:] - momentum_y[1:-1,0:-2]
            curl=curl_x-curl_y
            plt.clf()
            plt.imshow(curl,cmap='seismic')
            plt.imshow(array_test_r,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()

100%|██████████| 7000/7000 [04:43<00:00, 24.73it/s]


Can repeat rotated airfoil for one pointed down by swapping the negative signs for the sine functions. Can also put it at maximum angle of attack (at ~$15^\circ$)

### Critical Angle of Attack Testing

In [73]:
x_mid=np.median(xs_top)-20
y_low=min(ys_bottom)
y_high=max(ys_top)
y_mid=((y_high-y_low)//2)+y_low

In [99]:
x_top_rotation_c=(((xs_top-x_mid)*np.cos(np.pi/15))+x_mid)+(((ys_top-y_mid)*np.sin(np.pi/15))+y_mid)
y_top_rotation_c=(((xs_top-x_mid)*-np.sin(np.pi/15))+x_mid)+(((ys_top-y_mid)*np.cos(np.pi/15))+y_mid)
x_bottom_rotation_c=(((xs_bottom-x_mid)*np.cos(np.pi/15))+x_mid)+(((ys_bottom-y_mid)*np.sin(np.pi/15))+y_mid)
y_bottom_rotation_c=(((xs_bottom-x_mid)*-np.sin(np.pi/15))+x_mid)+(((ys_bottom-y_mid)*np.cos(np.pi/15))+y_mid)

In [100]:
x_min_r_c = int(min(x_top_rotation_c))
x_max_r_c = int(max(x_top_rotation_c))

x_length_airfoil_r_c = np.arange(x_min_r_c,x_max_r_c+1)
x_length_airfoil_shifted_r_c = x_length_airfoil_r_c-min(x_length_airfoil_r_c)
x_convert_airfoil_r_c = x_length_airfoil_shifted_r_c/max(x_length_airfoil_shifted_r_c)

In [101]:
def airfoil_single_r_c(x_val,y_len,y_shift):
    index=np.where(x_length_airfoil_r_c == x_val)[0]
    index_true=index[0]
    x = x_convert_airfoil_r_c[index_true]
    x_value=x_val
    t = thickness
    y_value = 5*t*(k0*np.sqrt(x)-k1*x-k2*x**2+k3*x**3-k4*x**4)
    y_top = (y_value*y_len)+y_shift
    y_top_r=(((x_value-x_mid)*np.sin(np.pi/15))+x_mid)+(((y_top-y_mid)*np.cos(np.pi/15))+y_mid)
    y_bottom = (-y_value*y_len)+y_shift
    y_bottom_r=(((x_value-x_mid)*np.sin(np.pi/15))+x_mid)+(((y_bottom-y_mid)*np.cos(np.pi/15))+y_mid)
    return y_top_r,y_bottom_r

In [102]:
plot_y_len_r_c=200
plot_x_len_r_c=400
array_test_r_c=np.zeros((plot_y_len_r_c,plot_x_len_r_c))
xs_used_c=[]
for y in range(0,plot_y_len_r_c):
    for x in range(0,plot_x_len_r_c):
        if x <= int(max(x_top_rotation_c)) and x >= int(min(x_top_rotation_c)):
            xs_used_c.append(x)
            if y <= airfoil_single_r_c(x,20,0)[0] and y >= airfoil_single_r_c(x,20,0)[1]:
                array_test_r_c[y-25,x] = 1
xs_used_c=np.unique(xs_used_c)

In [103]:
plt.imshow(array_test_r_c)
plt.show()

### Critical Angle of Attack Plotting

In [104]:
time_iterations=7000
plot_iterations=50

In [106]:
plot_shape_r_c = np.full((plot_y_len_r_c,plot_x_len_r_c),False)
for y in range(0,plot_y_len_r_c):
    for x in range(0,plot_x_len_r_c):
        if x <= int(max(x_top_rotation_c)) and x >= int(min(x_top_rotation_c)):
            if y <= airfoil_single_r_c(x,20,0)[0] and y >= airfoil_single_r_c(x,20,0)[1]:
                plot_shape_r_c[y-25,x] = True

In [107]:
array_test_r_c=np.zeros((plot_y_len_r_c,plot_x_len_r_c))
for y in range(0,plot_y_len_r_c):
    for x in range(0,plot_x_len_r_c):
        if x <= int(max(x_top_rotation_c)) and x >= int(min(x_top_rotation_c)):
            if y <= airfoil_single_r_c(x,20,0)[0] and y >= airfoil_single_r_c(x,20,0)[1]:
                array_test_r_c[y-25,x] = 1
                
for y in range(0,plot_y_len_r_c):
    for x in range(0,plot_x_len_r_c):
        if array_test_r_c[y,x] == 1 and array_test_r_c[y+1,x] == 0:
            array_test_r_c[y,x] = 10000
        elif array_test_r_c[y,x] == 1 and array_test_r_c[y-1,x] == 0:
            array_test_r_c[y,x] = 10000

In [96]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len_r_c,plot_x_len_r_c,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len_r_c,plot_x_len_r_c,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Critically_Roated_Airfoil_V1.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape_r_c,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape_r_c,:] = Collision_boundary_final
        momentum_x[plot_shape_r_c] = 0
        momentum_y[plot_shape_r_c] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            plt.clf()
            plt.imshow(np.sqrt(momentum_x**2+momentum_y**2),cmap='bone')
            plt.imshow(array_test_r_c,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.05)
            writer.grab_frame()

100%|██████████| 7000/7000 [04:50<00:00, 24.08it/s]


### Critical Angle of Attack Vorticity

In [108]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len_r_c,plot_x_len_r_c,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len_r_c,plot_x_len_r_c,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Critically_Roated_Airfoil_Vorticity_V2.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape_r_c,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape_r_c,:] = Collision_boundary_final
        momentum_x[plot_shape_r_c] = 0
        momentum_y[plot_shape_r_c] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            curl_x = momentum_x[2:,1:-1] - momentum_x[0:-2,1:-1]
            curl_y = momentum_y[1:-1,2:] - momentum_y[1:-1,0:-2]
            curl=curl_x-curl_y
            plt.clf()
            plt.imshow(curl,cmap='seismic')
            plt.show()
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()

100%|██████████| 7000/7000 [04:05<00:00, 28.57it/s]


### Downward Tilted Airfoil

In [12]:
x_mid=np.median(xs_top)-20
y_low=min(ys_bottom)
y_high=max(ys_top)
y_mid=((y_high-y_low)//2)+y_low

In [13]:
x_top_rotation_d=(((xs_top-x_mid)*np.cos(np.pi/6))+x_mid)+(((ys_top-y_mid)*-np.sin(np.pi/6))+y_mid)
y_top_rotation_d=(((xs_top-x_mid)*np.sin(np.pi/6))+x_mid)+(((ys_top-y_mid)*np.cos(np.pi/6))+y_mid)
x_bottom_rotation_d=(((xs_bottom-x_mid)*np.cos(np.pi/6))+x_mid)+(((ys_bottom-y_mid)*-np.sin(np.pi/6))+y_mid)
y_bottom_rotation_d=(((xs_bottom-x_mid)*np.sin(np.pi/6))+x_mid)+(((ys_bottom-y_mid)*np.cos(np.pi/6))+y_mid)

In [14]:
x_min_r_d = int(min(x_top_rotation_d))
x_max_r_d = int(max(x_top_rotation_d))

x_length_airfoil_r_d = np.arange(x_min_r_d,x_max_r_d+1)
x_length_airfoil_shifted_r_d = x_length_airfoil_r_d-min(x_length_airfoil_r_d)
x_convert_airfoil_r_d = x_length_airfoil_shifted_r_d/max(x_length_airfoil_shifted_r_d)

In [18]:
def airfoil_single_r_d(x_val,y_len,y_shift):
    index=np.where(x_length_airfoil_r_d == x_val)[0]
    index_true=index[0]
    x = x_convert_airfoil_r_d[index_true]
    x_value=x_val
    t = thickness
    y_value = 5*t*(k0*np.sqrt(x)-k1*x-k2*x**2+k3*x**3-k4*x**4)
    y_top = (y_value*y_len)+y_shift
    y_top_r=(((x_value-x_mid)*-np.sin(np.pi/6))+x_mid)+(((y_top-y_mid)*np.cos(np.pi/6))+y_mid)
    y_bottom = (-y_value*y_len)+y_shift
    y_bottom_r=(((x_value-x_mid)*-np.sin(np.pi/6))+x_mid)+(((y_bottom-y_mid)*np.cos(np.pi/6))+y_mid)
    return y_top_r,y_bottom_r

In [29]:
plot_y_len_r=200
plot_x_len_r=400
array_test_r_d=np.zeros((plot_y_len_r,plot_x_len_r))
xs_used=[]
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if x <= int(max(x_top_rotation_d)) and x >= int(min(x_top_rotation_d)):
            xs_used.append(x)
            if y <= airfoil_single_r_d(x,20,0)[0] and y >= airfoil_single_r_d(x,20,0)[1]:
                array_test_r_d[y+10,x] = 1
xs_used=np.unique(xs_used)

In [30]:
plt.imshow(array_test_r_d)
plt.show()

### Downward Plotting

In [36]:
time_iterations=7000
plot_iterations=50

In [37]:
plot_shape_r_d = np.full((plot_y_len_r,plot_x_len_r),False)
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if x <= int(max(x_top_rotation_d)) and x >= int(min(x_top_rotation_d)):
            if y <= airfoil_single_r_d(x,20,0)[0] and y >= airfoil_single_r_d(x,20,0)[1]:
                plot_shape_r_d[y+10,x] = True

In [38]:
array_test_r_d=np.zeros((plot_y_len_r,plot_x_len_r))
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if x <= int(max(x_top_rotation_d)) and x >= int(min(x_top_rotation_d)):
            if y <= airfoil_single_r_d(x,20,0)[0] and y >= airfoil_single_r_d(x,20,0)[1]:
                array_test_r_d[y+10,x] = 1
                
for y in range(0,plot_y_len_r):
    for x in range(0,plot_x_len_r):
        if array_test_r_d[y,x] == 1 and array_test_r_d[y+1,x] == 0:
            array_test_r_d[y,x] = 10000
        elif array_test_r_d[y,x] == 1 and array_test_r_d[y-1,x] == 0:
            array_test_r_d[y,x] = 10000

In [39]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len_r,plot_x_len_r,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len_r,plot_x_len_r,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Downwards_Airfoil_V1.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape_r_d,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape_r_d,:] = Collision_boundary_final
        momentum_x[plot_shape_r_d] = 0
        momentum_y[plot_shape_r_d] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            plt.clf()
            plt.imshow(np.sqrt(momentum_x**2+momentum_y**2),cmap='bone')
            plt.imshow(array_test_r_d,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.05)
            writer.grab_frame()

100%|██████████| 7000/7000 [05:03<00:00, 23.03it/s]


### Downward Vorticity

In [42]:
#Redefining inital conditions so it will run from start each time
Initial = np.ones((plot_y_len_r,plot_x_len_r,Number_of_lattice_particles))
Initial_random = Initial + randomness_cst*np.random.rand(plot_y_len_r,plot_x_len_r,Number_of_lattice_particles)
Main_array = Initial_random
Main_array[:,:,3] = 2.3

#mp4 stuff
metadata = dict(title='Lattice Boltzmann Fluid Over An Airfoil', artist='Sam Paplanus')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

with writer.saving(fig, "EPS_109_Project_Downwards_Vorticity_V2.mp4", dpi=200):
    for t in tqdm(range(time_iterations)):
        # Absorbing walls so we have no ripples; sticky boundary consitions
        #Sets particle of interest to have exact values of those diectly to side depending
        # on the wall we are looking at, killing it instantly
        
        # Right wall; 6,7,8 index of particles along the left side of the particle of interest
        Main_array[:,-1,(6,7,8)] =  Main_array[:,-2,(6,7,8)]
        # Left wall; 2,3,4 index of particles along the right side of the particle of interest
        Main_array[:,0,(2,3,4)] = Main_array[:,1,(2,3,4)]
        # Bottom wall; 8,1,2 index of particles along the top side of the particle of interest
        Main_array[-1,:,(8,1,2)] =  Main_array[-2,:,(8,1,2)]
        # Top wall; 4,5,6 index of particles along the bottom side of the particle of interest
        Main_array[0,:,(4,5,6)] = Main_array[1,:,(4,5,6)]
        
        for n,v_x,v_y in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions):
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_x, axis = 1)
            Main_array[:,:,n] = np.roll(Main_array[:,:,n], v_y, axis = 0)
            #Rolls the velocities along the designated axis
            #Using zip instead of 3 for loops saves significant amount of time

        #Calculating collisions with the airfoil
        Collision_boundary = Main_array[plot_shape_r_d,:]
        Collision_boundary_final = Collision_boundary[:,(0,5,6,7,8,1,2,3,4)] 
        #Previous line gives the particle the velocity of the particle opposite it on the lattice
        #It essentially rebounds the particle in the opposite direction

        #Defining fluid variables
        density=np.sum(Main_array,2)
        momentum_x = np.sum(Main_array*lattice_x_positions, 2)/density
        momentum_y = np.sum(Main_array*lattice_y_positions, 2)/density

        #Apply the boundaries so there is no fluid movement inside the airfoil
        Main_array[plot_shape_r_d,:] = Collision_boundary_final
        momentum_x[plot_shape_r_d] = 0
        momentum_y[plot_shape_r_d] = 0

        #Apply collisions from particles outside the airfoil
        velocity_equation = np.zeros(Main_array.shape)
        for n,v_X,v_Y,w in zip(range(Number_of_lattice_particles),lattice_x_positions,lattice_y_positions,lattice_movement_weights):
            velocity_equation[:,:,n] = density * w * (
                1+3*(v_X*momentum_x + v_Y*momentum_y) + 
                (9*(v_X*momentum_x + v_Y*momentum_y)**2)/2 - 
                3 *(momentum_x**2+momentum_y**2)/2
            )
        Main_array = Main_array + -(1/Tau) * (Main_array-velocity_equation)

        #Plotting
        if t%plot_iterations == 0:
            curl_x = momentum_x[2:,1:-1] - momentum_x[0:-2,1:-1]
            curl_y = momentum_y[1:-1,2:] - momentum_y[1:-1,0:-2]
            curl=curl_x-curl_y
            plt.clf()
            plt.imshow(curl,cmap='seismic')
            #plt.imshow(array_test_r_d,alpha=0.5,cmap='hot')
            plt.show()
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()

100%|██████████| 7000/7000 [04:08<00:00, 28.20it/s]
